In [15]:
import json

from branca.colormap import linear
import folium
from folium import Map, Marker, GeoJson, LayerControl
import pandas as pd
import geopandas as gpd

%matplotlib inline

## Load and explore geojson

In [16]:
gj_path = "geojson/anc.geojson"

In [17]:
anc_df = gpd.read_file(gj_path)

In [18]:
anc_df.head()

OBJECTID ANC_ID                                            WEB_URL    NAME  \
0         1     1C  http://anc.dc.gov/page/advisory-neighborhood-c...  ANC 1C   
1         2     1D  http://anc.dc.gov/page/advisory-neighborhood-c...  ANC 1D   
2         3     2A  http://anc.dc.gov/page/advisory-neighborhood-c...  ANC 2A   
3         4     2B  http://anc.dc.gov/page/advisory-neighborhood-c...  ANC 2B   
4         5     2C  http://anc.dc.gov/page/advisory-neighborhood-c...  ANC 2C   

     Shape_Leng    Shape_Area  \
0   5218.954361  1.285112e+06   
1   4224.010068  9.475922e+05   
2  12477.943204  7.065358e+06   
3   7712.504785  2.160620e+06   
4   7811.084627  2.861750e+06   

                                            geometry  
0  POLYGON ((-77.0464219248981 38.92597950466725,...  
1  POLYGON ((-77.03645123520528 38.93638367371454...  
2  POLYGON ((-77.05445304334567 38.90725341205063...  
3  POLYGON ((-77.0412259402753 38.91701561959232,...  
4  POLYGON ((-77.02404971019487 38.90293630338282...

## Preprocess data and join with election CSV using pandas

In [17]:
anc_df = pd.DataFrame([anc['properties'] for anc in ancs], columns = sorted(ancs[0]['properties'].keys()))
anc_df.head()

ANC_ID    NAME  OBJECTID    Shape_Area    Shape_Leng  \
0     1C  ANC 1C         1  1.285112e+06   5218.954361   
1     1D  ANC 1D         2  9.475922e+05   4224.010068   
2     2A  ANC 2A         3  7.065358e+06  12477.943204   
3     2B  ANC 2B         4  2.160620e+06   7712.504785   
4     2C  ANC 2C         5  2.861750e+06   7811.084627   

                                             WEB_URL  
0  http://anc.dc.gov/page/advisory-neighborhood-c...  
1  http://anc.dc.gov/page/advisory-neighborhood-c...  
2  http://anc.dc.gov/page/advisory-neighborhood-c...  
3  http://anc.dc.gov/page/advisory-neighborhood-c...  
4  http://anc.dc.gov/page/advisory-neighborhood-c...

In [11]:
election_df = pd.read_csv("election_data_for_anc_map.csv")
election_df.head()

ward  year anc  num_candidates       votes  vote_norm  engagement  \
0     1  2012   A        1.583333  481.500000        NaN         NaN   
1     1  2012   B        1.250000  544.333333        NaN         NaN   
2     1  2012   C        1.500000  641.875000        NaN         NaN   
3     1  2012   D        1.400000  559.800000        NaN         NaN   
4     1  2014   A        1.333333  296.250000   0.529246     0.63618   

   prop_uncontested  prop_empty  
0          0.500000         0.0  
1          0.916667         0.0  
2          0.625000         0.0  
3          0.600000         0.0  
4          0.666667         0.0

In [12]:
election_df["ANC_ID"] = election_df["ward"].map(str) + election_df["anc"]
election_df.drop(columns = ["ward", "anc"], inplace=True)
print(election_df.shape)
election_df.head()

(160, 8)


year  num_candidates       votes  vote_norm  engagement  prop_uncontested  \
0  2012        1.583333  481.500000        NaN         NaN          0.500000   
1  2012        1.250000  544.333333        NaN         NaN          0.916667   
2  2012        1.500000  641.875000        NaN         NaN          0.625000   
3  2012        1.400000  559.800000        NaN         NaN          0.600000   
4  2014        1.333333  296.250000   0.529246     0.63618          0.666667   

   prop_empty ANC_ID  
0         0.0     1A  
1         0.0     1B  
2         0.0     1C  
3         0.0     1D  
4         0.0     1A

In [13]:
election_df_2018 = election_df[election_df.year == 2018]
print(election_df_2018.shape)

(40, 8)


In [14]:
joined_df = anc_df.merge(election_df_2018, how="left", on="ANC_ID")
joined_df.head()

OBJECTID ANC_ID                                            WEB_URL    NAME  \
0         1     1C  http://anc.dc.gov/page/advisory-neighborhood-c...  ANC 1C   
1         2     1D  http://anc.dc.gov/page/advisory-neighborhood-c...  ANC 1D   
2         3     2A  http://anc.dc.gov/page/advisory-neighborhood-c...  ANC 2A   
3         4     2B  http://anc.dc.gov/page/advisory-neighborhood-c...  ANC 2B   
4         5     2C  http://anc.dc.gov/page/advisory-neighborhood-c...  ANC 2C   

     Shape_Leng    Shape_Area  \
0   5218.954361  1.285112e+06   
1   4224.010068  9.475922e+05   
2  12477.943204  7.065358e+06   
3   7712.504785  2.160620e+06   
4   7811.084627  2.861750e+06   

                                            geometry  year  num_candidates  \
0  POLYGON ((-77.0464219248981 38.92597950466725,...  2018        1.375000   
1  POLYGON ((-77.03645123520528 38.93638367371454...  2018        1.600000   
2  POLYGON ((-77.05445304334567 38.90725341205063...  2018        1.125000   
3  POLYGON ((-77.0412259402753 38.91701561959232,...  2018        1.222222   
4  POLYGON ((-77.02404971019487 38.90293630338282...  2018        1.333333   

        votes  vote_norm  engagement  prop_uncontested  prop_empty  
0  690.500000   0.695144    0.818804          0.625000         0.0  
1  513.200000   0.608100    0.818987          0.400000         0.0  
2  254.375000   0.688037    0.770138          0.875000         0.0  
3  574.666667   0.698349    0.840883          0.777778         0.0  
4  417.000000   0.686430    0.806862          0.666667         0.0

## Update geojson features from dataframe values

In [89]:
""" No longer necessary
for anc in gjdata['features']:
    anc_id = anc['properties']['ANC_ID']
    features = election_df.columns.tolist()
    features.remove("ANC_ID")
    for feature in features:
        anc['properties'][feature] = joined_df.loc[joined_df['ANC_ID'] == anc_id, feature].item()
"""

' No longer necessary\nfor anc in gjdata[\'features\']:\n    anc_id = anc[\'properties\'][\'ANC_ID\']\n    features = election_df.columns.tolist()\n    features.remove("ANC_ID")\n    for feature in features:\n        anc[\'properties\'][feature] = joined_df.loc[joined_df[\'ANC_ID\'] == anc_id, feature].item()\n'

## Construct map

In [39]:
anc_map = Map(location = (38.8899, -77.0091),
              zoom_start = 12,
              tiles = 'Stamen Toner')

In [40]:
folium.Choropleth(
    geo_data=gj_path,
    data=joined_df,
    columns=["ANC_ID", "votes"],
    key_on='feature.properties.ANC_ID',
    fill_color='GnBu',
    fill_opacity=0.5,
    line_weight=1,  
    highlight=True,
    overlay=True,
    name="average votes",
    legend_name="average # votes for winning candidates",
).add_to(anc_map)

In [41]:
folium.Choropleth(
    geo_data=gj_path,
    data=joined_df,
    columns=["ANC_ID", "engagement"],
    key_on='feature.properties.ANC_ID',
    fill_color='PuRd',
    fill_opacity=0.5,
    line_weight=1,  
    highlight=True,
    overlay=True,
    name="engagement",
    legend_name="percentage of ballots where ANC candidate was marked",
).add_to(anc_map)

In [42]:
LayerControl().add_to(anc_map)

In [43]:
anc_map